# Construir um modelo de regressão: preparar e visualizar dados

## **Regressão Linear para Abóboras - Aula 2**
#### Introdução

Agora que já tem as ferramentas necessárias para começar a construir modelos de machine learning com Tidymodels e Tidyverse, está pronto para começar a fazer perguntas aos seus dados. Ao trabalhar com dados e aplicar soluções de ML, é muito importante saber como formular a pergunta certa para desbloquear adequadamente o potencial do seu conjunto de dados.

Nesta aula, irá aprender:

-   Como preparar os seus dados para a construção de modelos.

-   Como usar `ggplot2` para visualização de dados.

A pergunta que precisa de responder determinará o tipo de algoritmos de ML que irá utilizar. E a qualidade da resposta que obtém dependerá fortemente da natureza dos seus dados.

Vamos ver isso através de um exercício prático.

<p >
   <img src="../../images/unruly_data.jpg"
   width="700"/>
   <figcaption>Arte por @allison_horst</figcaption>


## 1. Importar dados de abóboras e invocar o Tidyverse

Vamos precisar dos seguintes pacotes para explorar esta lição:

-   `tidyverse`: O [tidyverse](https://www.tidyverse.org/) é uma [coleção de pacotes R](https://www.tidyverse.org/packages) projetada para tornar a ciência de dados mais rápida, fácil e divertida!

Pode instalá-los com o seguinte comando:

`install.packages(c("tidyverse"))`

O script abaixo verifica se tem os pacotes necessários para completar este módulo e instala-os caso algum esteja em falta.


In [ ]:
suppressWarnings(if(!require("pacman")) install.packages("pacman"))
pacman::p_load(tidyverse)

Agora, vamos ativar alguns pacotes e carregar os [dados](https://github.com/microsoft/ML-For-Beginners/blob/main/2-Regression/data/US-pumpkins.csv) fornecidos para esta lição!


In [ ]:
# Load the core Tidyverse packages
library(tidyverse)

# Import the pumpkins data
pumpkins <- read_csv(file = "https://raw.githubusercontent.com/microsoft/ML-For-Beginners/main/2-Regression/data/US-pumpkins.csv")


# Get a glimpse and dimensions of the data
glimpse(pumpkins)


# Print the first 50 rows of the data set
pumpkins %>% 
  slice_head(n =50)

Um rápido `glimpse()` mostra imediatamente que há espaços em branco e uma mistura de strings (`chr`) e dados numéricos (`dbl`). A `Date` é do tipo carácter e há também uma coluna estranha chamada `Package`, onde os dados são uma mistura entre `sacks`, `bins` e outros valores. Os dados, na verdade, estão um pouco desorganizados 😤.

De facto, não é muito comum receber um conjunto de dados completamente pronto para usar e criar um modelo de ML diretamente. Mas não se preocupe, nesta lição, irá aprender como preparar um conjunto de dados bruto utilizando bibliotecas padrão do R 🧑‍🔧. Também irá aprender várias técnicas para visualizar os dados.📈📊
<br>

> Um lembrete: O operador pipe (`%>%`) realiza operações numa sequência lógica ao passar um objeto para uma função ou expressão. Pode pensar no operador pipe como dizendo "e depois" no seu código.


## 2. Verificar dados em falta

Um dos problemas mais comuns que os cientistas de dados enfrentam é lidar com dados incompletos ou em falta. O R representa valores em falta, ou desconhecidos, com um valor especial chamado `NA` (Not Available).

Então, como podemos saber se o data frame contém valores em falta?
<br>
-   Uma forma direta seria usar a função base do R `anyNA`, que retorna os objetos lógicos `TRUE` ou `FALSE`.


In [ ]:
pumpkins %>% 
  anyNA()

Ótimo, parece que há alguns dados em falta! Esse é um bom ponto de partida.

-   Outra forma seria usar a função `is.na()` que indica quais elementos individuais das colunas estão em falta com um valor lógico `TRUE`.


In [ ]:
pumpkins %>% 
  is.na() %>% 
  head(n = 7)

Ok, trabalho concluído, mas com um conjunto de dados tão grande como este, seria ineficiente e praticamente impossível rever todas as linhas e colunas individualmente😴.

-   Uma forma mais intuitiva seria calcular a soma dos valores em falta para cada coluna:


In [ ]:
pumpkins %>% 
  is.na() %>% 
  colSums()

Muito melhor! Faltam alguns dados, mas talvez isso não seja relevante para a tarefa em questão. Vamos ver que tipo de análise adicional pode surgir.

> Além dos conjuntos incríveis de pacotes e funções, o R possui uma documentação muito boa. Por exemplo, use `help(colSums)` ou `?colSums` para saber mais sobre a função.


## 3. Dplyr: Uma Gramática para Manipulação de Dados

<p >
   <img src="../../images/dplyr_wrangling.png"
   width="569"/>
   <figcaption>Ilustração por @allison_horst</figcaption>


<!--![Ilustração por \@allison_horst](../../../../../../translated_images/dplyr_wrangling.f5f99c64fd4580f1377fee3ea428b6f8fd073845ec0f8409d483cfe148f0984e.pt.png)<br/>Ilustração por \@allison_horst-->


[`dplyr`](https://dplyr.tidyverse.org/), um pacote do Tidyverse, é uma gramática de manipulação de dados que oferece um conjunto consistente de verbos para ajudar a resolver os desafios mais comuns de manipulação de dados. Nesta seção, vamos explorar alguns dos verbos do dplyr!


#### dplyr::select()

`select()` é uma função do pacote `dplyr` que ajuda a escolher colunas para manter ou excluir.

Para tornar o seu data frame mais fácil de trabalhar, elimine várias das suas colunas, utilizando `select()`, mantendo apenas as colunas necessárias.

Por exemplo, neste exercício, a nossa análise irá envolver as colunas `Package`, `Low Price`, `High Price` e `Date`. Vamos selecionar estas colunas.


In [ ]:
# Select desired columns
pumpkins <- pumpkins %>% 
  select(Package, `Low Price`, `High Price`, Date)


# Print data set
pumpkins %>% 
  slice_head(n = 5)

#### dplyr::mutate()

`mutate()` é uma função do pacote `dplyr` que ajuda a criar ou modificar colunas, mantendo as colunas existentes.

A estrutura geral do `mutate` é:

`data %>%   mutate(new_column_name = what_it_contains)`

Vamos experimentar o `mutate` utilizando a coluna `Date` e realizar as seguintes operações:

1. Converter as datas (atualmente do tipo carácter) para um formato de mês (estas são datas dos EUA, então o formato é `MM/DD/YYYY`).

2. Extrair o mês das datas para uma nova coluna.

Em R, o pacote [lubridate](https://lubridate.tidyverse.org/) facilita o trabalho com dados de data e hora. Então, vamos usar `dplyr::mutate()`, `lubridate::mdy()`, `lubridate::month()` e ver como alcançar os objetivos acima. Podemos eliminar a coluna `Date`, já que não será mais necessária em operações subsequentes.


In [ ]:
# Load lubridate
library(lubridate)

pumpkins <- pumpkins %>% 
  # Convert the Date column to a date object
  mutate(Date = mdy(Date)) %>% 
  # Extract month from Date
  mutate(Month = month(Date)) %>% 
  # Drop Date column
  select(-Date)

# View the first few rows
pumpkins %>% 
  slice_head(n = 7)

Uhuu! 🤩

A seguir, vamos criar uma nova coluna `Price`, que representa o preço médio de uma abóbora. Agora, vamos calcular a média das colunas `Low Price` e `High Price` para preencher a nova coluna Price.
<br>


In [ ]:
# Create a new column Price
pumpkins <- pumpkins %>% 
  mutate(Price = (`Low Price` + `High Price`)/2)

# View the first few rows of the data
pumpkins %>% 
  slice_head(n = 5)

Sim!💪

"Mas espera aí!", dirás depois de examinar todo o conjunto de dados com `View(pumpkins)`, "Há algo estranho aqui!"🤔

Se olhares para a coluna `Package`, as abóboras são vendidas em várias configurações diferentes. Algumas são vendidas em medidas de `1 1/9 bushel`, outras em medidas de `1/2 bushel`, algumas por abóbora, outras por peso, e algumas em grandes caixas com larguras variadas.

Vamos verificar isto:


In [ ]:
# Verify the distinct observations in Package column
pumpkins %>% 
  distinct(Package)

Incrível!👏

As abóboras parecem ser muito difíceis de pesar de forma consistente, por isso vamos filtrá-las selecionando apenas as abóboras com a palavra *bushel* na coluna `Package` e colocar isso num novo quadro de dados `new_pumpkins`.


#### dplyr::filter() e stringr::str_detect()

[`dplyr::filter()`](https://dplyr.tidyverse.org/reference/filter.html): cria um subconjunto dos dados contendo apenas as **linhas** que satisfazem as suas condições, neste caso, abóboras com a string *bushel* na coluna `Package`.

[stringr::str_detect()](https://stringr.tidyverse.org/reference/str_detect.html): deteta a presença ou ausência de um padrão numa string.

O pacote [`stringr`](https://github.com/tidyverse/stringr) fornece funções simples para operações comuns com strings.


In [ ]:
# Retain only pumpkins with "bushel"
new_pumpkins <- pumpkins %>% 
       filter(str_detect(Package, "bushel"))

# Get the dimensions of the new data
dim(new_pumpkins)

# View a few rows of the new data
new_pumpkins %>% 
  slice_head(n = 5)

Pode ver que reduzimos para cerca de 415 linhas de dados contendo abóboras por alqueire.🤩  


#### dplyr::case_when()

**Mas espera! Ainda há algo mais a fazer**

Reparaste que a quantidade por alqueire varia por linha? É necessário normalizar os preços para que sejam apresentados por alqueire, e não por 1 1/9 ou 1/2 alqueire. Está na hora de fazer alguns cálculos para os padronizar.

Vamos usar a função [`case_when()`](https://dplyr.tidyverse.org/reference/case_when.html) para *alterar* a coluna Price com base em algumas condições. `case_when` permite vectorizar múltiplas instruções `if_else()`.


In [ ]:
# Convert the price if the Package contains fractional bushel values
new_pumpkins <- new_pumpkins %>% 
  mutate(Price = case_when(
    str_detect(Package, "1 1/9") ~ Price/(1 + 1/9),
    str_detect(Package, "1/2") ~ Price/(1/2),
    TRUE ~ Price))

# View the first few rows of the data
new_pumpkins %>% 
  slice_head(n = 30)

Agora podemos analisar o preço por unidade com base na sua medida em alqueires. Todo este estudo sobre alqueires de abóboras, no entanto, mostra como é `importante` `compreender a natureza dos seus dados`!

> ✅ De acordo com [The Spruce Eats](https://www.thespruceeats.com/how-much-is-a-bushel-1389308), o peso de um alqueire depende do tipo de produto, já que é uma medida de volume. "Um alqueire de tomates, por exemplo, deve pesar 56 libras... Folhas e verduras ocupam mais espaço com menos peso, então um alqueire de espinafre pesa apenas 20 libras." É tudo bastante complicado! Não vamos nos preocupar em fazer uma conversão de alqueires para libras e, em vez disso, vamos precificar por alqueire. Todo este estudo sobre alqueires de abóboras, no entanto, mostra como é muito importante compreender a natureza dos seus dados!
>
> ✅ Reparaste que as abóboras vendidas por meio alqueire são muito caras? Consegues descobrir porquê? Dica: abóboras pequenas são muito mais caras do que as grandes, provavelmente porque há muito mais delas por alqueire, considerando o espaço não utilizado ocupado por uma grande abóbora oca para tartes.


Agora, por pura diversão 💁‍♀️, vamos também mover a coluna Mês para a primeira posição, ou seja, `antes` da coluna `Pacote`.

`dplyr::relocate()` é usado para alterar as posições das colunas.


In [ ]:
# Create a new data frame new_pumpkins
new_pumpkins <- new_pumpkins %>% 
  relocate(Month, .before = Package)

new_pumpkins %>% 
  slice_head(n = 7)

Bom trabalho!👌 Agora tens um conjunto de dados limpo e organizado para construir o teu novo modelo de regressão!


## 4. Visualização de dados com ggplot2

<p >
   <img src="../../images/data-visualization.png"
   width="600"/>
   <figcaption>Infografia por Dasani Madipalli</figcaption>


<!--![Infografia por Dasani Madipalli](../../../../../../translated_images/data-visualization.54e56dded7c1a804d00d027543f2881cb32da73aeadda2d4a4f10f3497526114.pt.png){width="600"}-->

Há um ditado *sábio* que diz o seguinte:

> "O gráfico simples trouxe mais informação à mente do analista de dados do que qualquer outro dispositivo." --- John Tukey

Parte do papel do cientista de dados é demonstrar a qualidade e a natureza dos dados com os quais está a trabalhar. Para isso, muitas vezes criam visualizações interessantes, ou gráficos, diagramas e tabelas, que mostram diferentes aspetos dos dados. Desta forma, conseguem mostrar visualmente relações e lacunas que, de outra forma, seriam difíceis de identificar.

As visualizações também podem ajudar a determinar a técnica de machine learning mais adequada para os dados. Um gráfico de dispersão que parece seguir uma linha, por exemplo, indica que os dados são bons candidatos para um exercício de regressão linear.

O R oferece vários sistemas para criar gráficos, mas o [`ggplot2`](https://ggplot2.tidyverse.org/index.html) é um dos mais elegantes e versáteis. O `ggplot2` permite compor gráficos **combinando componentes independentes**.

Vamos começar com um simples gráfico de dispersão para as colunas Price e Month.

Neste caso, começaremos com [`ggplot()`](https://ggplot2.tidyverse.org/reference/ggplot.html), fornecendo um conjunto de dados e um mapeamento estético (com [`aes()`](https://ggplot2.tidyverse.org/reference/aes.html)) e, em seguida, adicionaremos camadas (como [`geom_point()`](https://ggplot2.tidyverse.org/reference/geom_point.html)) para gráficos de dispersão.


In [ ]:
# Set a theme for the plots
theme_set(theme_light())

# Create a scatter plot
p <- ggplot(data = new_pumpkins, aes(x = Price, y = Month))
p + geom_point()

É um gráfico útil 🤷? Há algo nele que te surpreenda?

Não é particularmente útil, pois tudo o que faz é mostrar os teus dados como uma dispersão de pontos num determinado mês.
<br>


### **Como torná-lo útil?**

Para que os gráficos exibam dados úteis, normalmente é necessário agrupar os dados de alguma forma. Por exemplo, no nosso caso, calcular o preço médio das abóboras para cada mês proporcionaria mais insights sobre os padrões subjacentes nos nossos dados. Isso leva-nos a mais uma abordagem rápida do **dplyr**:

#### `dplyr::group_by() %>% summarize()`

A agregação agrupada em R pode ser facilmente calculada usando

`dplyr::group_by() %>% summarize()`

-   `dplyr::group_by()` altera a unidade de análise do conjunto de dados completo para grupos individuais, como por mês.

-   `dplyr::summarize()` cria um novo data frame com uma coluna para cada variável de agrupamento e uma coluna para cada estatística resumida que especificares.

Por exemplo, podemos usar `dplyr::group_by() %>% summarize()` para agrupar as abóboras com base na coluna **Month** e, em seguida, calcular o **preço médio** para cada mês.


In [ ]:
# Find the average price of pumpkins per month
new_pumpkins %>%
  group_by(Month) %>% 
  summarise(mean_price = mean(Price))

Sucinto!✨

Características categóricas, como meses, são melhor representadas utilizando um gráfico de barras 📊. As camadas responsáveis pelos gráficos de barras são `geom_bar()` e `geom_col()`. Consulte `?geom_bar` para saber mais.

Vamos criar um agora!


In [ ]:
# Find the average price of pumpkins per month then plot a bar chart
new_pumpkins %>%
  group_by(Month) %>% 
  summarise(mean_price = mean(Price)) %>% 
  ggplot(aes(x = Month, y = mean_price)) +
  geom_col(fill = "midnightblue", alpha = 0.7) +
  ylab("Pumpkin Price")

🤩🤩Esta é uma visualização de dados mais útil! Parece indicar que o preço mais alto das abóboras ocorre em setembro e outubro. Isso corresponde às suas expectativas? Porquê ou porquê não?

Parabéns por concluir a segunda lição 👏! Preparou os seus dados para a construção do modelo e, em seguida, descobriu mais informações através de visualizações!



---

**Aviso Legal**:  
Este documento foi traduzido utilizando o serviço de tradução por IA [Co-op Translator](https://github.com/Azure/co-op-translator). Embora nos esforcemos para garantir a precisão, é importante notar que traduções automáticas podem conter erros ou imprecisões. O documento original na sua língua nativa deve ser considerado a fonte autoritária. Para informações críticas, recomenda-se a tradução profissional realizada por humanos. Não nos responsabilizamos por quaisquer mal-entendidos ou interpretações incorretas decorrentes do uso desta tradução.
